## What is SCTK ? 

- The NIST Scoring Toolkit or SCTK for short, is a command line tool that offers ways to score and compare text transcripts.

- It can generate several types of reports that can be used to identify systematic errors and other common mistakes made by an ASR system.

- Go-SCTK is a wrapper around the original SCTK toolkit that offers a simplified interface, and formats the reports better for languages that don't use an ASCII script.


## Download Go-SCTK tool

In [1]:
# Getting Go SCTK CLI tool and giving it executable permissions.
!version=v0.3.0 && wget -q -O sctk https://github.com/shahruk10/go-sctk/releases/download/${version}/sctk && chmod +x ./sctk

# Printing usage docs.
!./sctk score --help

USAGE
  
sctk score \
  --ignore-first=true --delimiter="," --col-id=1 --col-trn=2 \
  --case-sensitive=false --normalize-unicode=true \
  --out=./wer --ref=truth.csv --hyp=output1.csv


FLAGS
  -case-sensitive=false  If true, scoring will be case sensitive.

  -cer=false  If true, will evaluate character error rate instead of word error rate.

  -col-id 0  The column index (zero based, positive only) containing <utteranceID>.

  -col-trn 1  The column index (zero based, positive only) containing <transcript>.

  -delimiter ,  The delimiter used in reference and hypotheses files. By default, the program expects
comma delimited files (.csv) The program needs at least two columns per row, containing
<utteranceID> and <transcript>. By default, the first and second columns are assumed
to contain <utteranceID> and <transcript> respectively. This can be changed by using
--id-col and --trn-col arguments.

  -encoding utf-8  What text encoding to use for interpreting text.

  -hyp ...  (Requir

## Transcribe validation set using pretrained model

- First let's generate some results using a pretrained off-the-shelf model

In [2]:
!pip install jiwer

In [2]:
from typing import Dict, List, Tuple, Any, Union

import os

import numpy as np
import pandas as pd
import json

import transformers
from transformers import Wav2Vec2ForCTC, pipeline
from datasets import load_metric

from tqdm.auto import tqdm
from IPython.display import display, Audio, HTML

cer = load_metric("cer")
wer = load_metric("wer")
import warnings 
warnings.filterwarnings('ignore')

In [3]:
!git clone https://gitlab.com/mushrafi88/dlsprint.git

Cloning into 'dlsprint'...
remote: Enumerating objects: 84, done.
remote: Counting objects: 100% (84/84), done.
remote: Compressing objects: 100% (79/79), done.
remote: Total 84 (delta 37), reused 0 (delta 0), pack-reused 0
Receiving objects: 100% (84/84), 15.05 MiB | 887.00 KiB/s, done.
Resolving deltas: 100% (37/37), done.


## Evaluate predictions using SCTK

- We can now provide our predictions and reference transcripts to SCTK for analysis.
- We could also use outputs from other models / previous iterations of models as the reference as well. This will highlight the things that changed between models.

In [2]:
def space_remover(x):
    return " ".join(x.split())

In [3]:
def remove_punctuations(my_str):
    punctuations = '''````£|¢|Ñ+-*/=EROero৳০১২৩৪৫৬৭৮৯012–34567•89।!()-[]{};:'"“\’…,<>.‚/?@#$%^&*_~‘—॥”‰🤣⚽️✌�￰৷￰'''
    no_punct = ""
    for char in my_str:
        if char not in punctuations:
            no_punct = no_punct + char
    return no_punct

In [4]:
valid = pd.read_csv('dlsprint/validation_with_spelling.csv')

In [17]:
valid_ref=valid.drop(['predicted', 'cor', 'Sub', 'Del', 'Ins'],axis=1)
valid_pred = valid.drop(['actual', 'cor', 'Sub', 'Del', 'Ins'],axis=1)

In [18]:
valid_pred.to_csv('valid_pred.csv',index=False)
valid_ref.to_csv('valid_ref.csv',index=False)

In [19]:
valid_ref

path  \
0     common_voice_bn_31600769.mp3   
1     common_voice_bn_31513081.mp3   
2     common_voice_bn_31630830.mp3   
3     common_voice_bn_31534395.mp3   
4     common_voice_bn_31509995.mp3   
...                            ...   
2935  common_voice_bn_31791024.mp3   
2936  common_voice_bn_31541317.mp3   
2937  common_voice_bn_30998753.mp3   
2938  common_voice_bn_30998861.mp3   
2939  common_voice_bn_31515356.mp3   

                                                 actual  
0     শিখর ধাওয়ান তার প্রথম আন্তর্জাতিক উইকেট শিকারে...  
1     চতুর্থ সপ্তাহ থেকে অবস্থার উন্নতি হতে থাকেকিন্...  
2              শীতকালীন গেমসে এখনো কোন পদক জিততে পারেনি  
3                  তিনি এথেন্সে এসে সক্রেটিসের শিষ্য হন  
4     নিষিদ্ধ আদেশ তৎক্ষণাৎ শহরের উপর চাপিয়ে দেওয়া হ...  
...                                                 ...  
2935  কৃষ্ণ তাকে কুরুক্ষেত্রের যুদ্ধের বিধ্বংসী বিবর...  
2936  একুশ বছর বয়সে রচিত এ উপন্যাসকে ছফা নিজেই নিজের...  
2937  তেলুগু ফিল্ম ইন্ডাস্ট্রিতে এই ঘটনার প্রেক্ষাপট...  
2938     গমের আটা এবং পুরো গমের ময়দার মধ্যে পার্থক্য কী  
2939  কুয়ালালামপুর আন্তর্জাতিক বিমানবন্দর মালয়েশিয়ার...  

[2940 rows x 2 columns]

In [20]:
# Running sctk on model output for the validation set.
# 
# Since the first row in the file contains headers, we set --ignore-first=true
#
# The file ID is the first column (index = 0) and the transcripts
# are in the second column (index = 1); so setting --col-id and
# --col-trn to 0 and 1 respectively.
#
# By setting --cer=false, we are evaluating at the word level.
!./sctk score \
  --ignore-first=true \
  --delimiter="," \
  --col-id=0 \
  --col-trn=1 \
  --cer=false \
  --out=report \
  --ref=valid_ref.csv \
  --hyp=valid_pred.csv

- SCTK generates a bunch of files. Let's take a look at some.

- First, the `*.dtl` file contains a detailed breakdown of the different errors; there are three sections: `Confusion Pairs` or `Substitutions`, `Deletions` and `Insertions`.

In [21]:
display(HTML(open("./report/hyp1.trn.dtl", 'r').read().replace("\n", "<br>")))

- Next, let's take a look at the `*.pra` file. This contains alignments between the reference and model output. This is provided in a variety of formats. HTML is probably the easiest to view in a notebook.

 - Sidenote, these alignments can also be used to combine the outputs from different ASR models (See [ROVER](https://ieeexplore.ieee.org/document/659110) algorithm).


In [22]:
display(HTML(open("./report/hyp1.trn.pra.html", 'r').read()))

In [23]:
import json
 
# Opening JSON file
with open('report/hyp1.trn.pra.json') as json_file:
    data = json.load(json_file)

In [28]:
data.keys()

dict_keys(['system_name', 'speakers'])

In [39]:
l=list(data['speakers']['common'].keys())
l[:5]

['(common_voice_bn_30635672.mp3)',
 '(common_voice_bn_30635673.mp3)',
 '(common_voice_bn_30661746.mp3)',
 '(common_voice_bn_30661747.mp3)',
 '(common_voice_bn_30664799.mp3)']

In [46]:
len(l)

2940

In [53]:
data['speakers']['common'][l[0]]

{'SystemName': 'hyp1',
 'SpeakerID': 'common',
 'sentence_id': '(common_voice_bn_30635672.mp3)',
 'sequence': 2618,
 'word_count': 6,
 'words': [{'eval_label': 'C', 'ref': 'পরবর্তীকালে', 'hyp': 'পরবর্তীকালে'},
  {'eval_label': 'C', 'ref': 'ক্লাব', 'hyp': 'ক্লাব'},
  {'eval_label': 'C', 'ref': 'ক্রিকেটের', 'hyp': 'ক্রিকেটের'},
  {'eval_label': 'C', 'ref': 'দিকে', 'hyp': 'দিকে'},
  {'eval_label': 'S', 'ref': 'ধাবিত', 'hyp': 'ধাপিত'},
  {'eval_label': 'C', 'ref': 'হন', 'hyp': 'হন'}]}

In [ ]:
df_errors = pd.DataFrame()
for i in range(len(l)):
    temp=data['speakers']['common'][l[i]]
    sen_id=temp['sentence_id']
    sen_id=sen_id[1:-1]
    words=temp['words']
    for elements in words:
        if elements['eval_label'] != 'C':
            dict = {'path': sen_id, 'ref': elements['ref'], 'hyp': elements['hyp']}
            df_errors = df_errors.append(dict, ignore_index = True)

In [78]:
df_errors.to_csv('validation_error_list.csv',index=False)

In [79]:
df_errors

path              ref          hyp
0     common_voice_bn_30635672.mp3            ধাবিত        ধাপিত
1     common_voice_bn_30635673.mp3        মধ্যবিত্ত      মধ্যবিত
2     common_voice_bn_30635673.mp3           পিছিয়ে         পিছে
3     common_voice_bn_30661746.mp3        ছাগলনাইয়া    ছাকলনায়য়া
4     common_voice_bn_30661747.mp3              করে             
...                            ...              ...          ...
5719  common_voice_bn_31791024.mp3         বিধ্বংসী     বিদ্ধংশী
5720  common_voice_bn_31798449.mp3                      পুরস্কার
5721  common_voice_bn_31798449.mp3  পুরস্কারপ্রাপ্ত      প্রাপ্ত
5722  common_voice_bn_31810695.mp3      দীর্ঘমেয়াদি   দী্ঘমেরাদি
5723  common_voice_bn_31811475.mp3     উদ্বাস্তুদের  উদ্বাস্তদের

[5724 rows x 3 columns]

## For any csv file

In [3]:
df = pd.read_csv('2.csv')
#df = df.drop('punctuation',axis=1)
#format path,actual,predicted(no punct)

In [5]:
valid_ref=df.drop('spelling',axis=1)
valid_pred = df.drop('sentence',axis=1)

In [6]:
valid_pred.to_csv('valid_pred.csv',index=False)
valid_ref.to_csv('valid_ref.csv',index=False)

In [122]:
df = df.drop(['predicted','predicted_raw'],axis=1)

In [123]:
df.columns

Index(['path', 'actual', 'spelling'], dtype='object')

In [124]:
def space_remover(x):
    return " ".join(x.split())

In [125]:
def remove_punctuations(my_str):
    punctuations = '''````£|¢|Ñ+-*/=EROero৳০১২৩৪৫৬৭৮৯012–34567•89।!()-[]{};:'"“\’…,<>.‚/?@#$%^&*_~‘—॥”‰🤣⚽️✌�￰৷￰'''
    no_punct = " "
    for char in my_str:
        if char not in punctuations:
            no_punct = no_punct + char
    return no_punct

In [126]:
def error_list(df):
    valid_ref=df.drop('spelling',axis=1)
    valid_pred = df.drop('actual',axis=1)
    valid_ref['actual'] = valid_ref['actual'].apply(lambda x : remove_punctuations(x))
    valid_pred['spelling']=valid_pred['spelling'].apply(lambda x: space_remover(str(x)))
    valid_pred.to_csv('valid_pred.csv',index=False)
    valid_ref.to_csv('valid_ref.csv',index=False)

In [127]:
error_list(df)

In [7]:
!./sctk score \
  --ignore-first=true \
  --delimiter="," \
  --col-id=0 \
  --col-trn=1 \
  --cer=false \
  --out=report_temp \
  --ref=valid_ref.csv \
  --hyp=valid_pred.csv

In [ ]:
display(HTML(open("./report_temp/hyp1.trn.dtl", 'r').read().replace("\n", "<br>")))

In [ ]:
display(HTML(open("./report_temp/hyp1.trn.pra.html", 'r').read()))

In [8]:
import json
with open('report_temp/hyp1.trn.pra.json') as json_file:
    data = json.load(json_file)

In [9]:
df_errors = pd.DataFrame()

In [10]:
l=list(data['speakers']['common'].keys())

In [11]:
for i in range(len(l)):
    temp=data['speakers']['common'][l[i]]
    sen_id=temp['sentence_id']
    sen_id=sen_id[1:-1]
    words=temp['words']
    for elements in words:
        if elements['eval_label'] != 'C':
            dict = {'path': sen_id, 'ref': elements['ref'], 'hyp': elements['hyp']}
            df_errors = df_errors.append(dict, ignore_index = True)

In [12]:
df_errors = df_errors.replace(r'^\s*$', np.nan, regex=True)
df_errors = df_errors.dropna()
df_errors

path         ref        hyp
0     common_voice_bn_30992467.mp3      পিমকুক     কিরকুক
1     common_voice_bn_30992467.mp3   এয়লাবামায়   এলাবামায়
2     common_voice_bn_30993879.mp3   টরেন্টরতে  টরেন্টোতে
3     common_voice_bn_30995382.mp3     সর্বর্হ    সর্বরাহ
4     common_voice_bn_30997157.mp3     রাহুলএর    রাহুলের
...                            ...         ...        ...
1123  common_voice_bn_31786955.mp3    চিরালায়।    নিরালায়
1124  common_voice_bn_31788420.mp3  রক্তপূণিকা  রক্তকণিকা
1125  common_voice_bn_31792299.mp3     জিটিএএর      জিটিএ
1126  common_voice_bn_31795509.mp3   স্বয়চ্ছায়  স্বেচ্ছায়
1127  common_voice_bn_31804077.mp3           ।          ও

[1020 rows x 3 columns]

In [13]:
df_errors.to_csv('error_list.csv',index=False)

In [77]:
df_errors

path              ref         hyp
0     common_voice_bn_30635673.mp3        মধ্যবিত্ত     মধ্যবিত
1     common_voice_bn_30635673.mp3           পিছিয়ে        পিছে
2     common_voice_bn_30661746.mp3        ছাগলনাইয়া   ছাকলনায়য়া
4     common_voice_bn_30661747.mp3            ছিলেন    করেছিলেন
5     common_voice_bn_30664799.mp3         জ্যেষ্ঠা      যোজ্ঠা
...                            ...              ...         ...
5756  common_voice_bn_31787482.mp3        জামশেদপুর          বা
5757  common_voice_bn_31788235.mp3            পুলিস       পুলিশ
5759  common_voice_bn_31791024.mp3         বিধ্বংসী    বিদ্ধংশী
5761  common_voice_bn_31798449.mp3  পুরস্কারপ্রাপ্ত     প্রাপ্ত
5762  common_voice_bn_31810695.mp3      দীর্ঘমেয়াদি  দী্ঘমেরাদি

[4230 rows x 3 columns]

### Evaluating at the character level.

- We can run the same analysis as above at the character level instead of words.

In [14]:
# Running sctk on model output for the validation set.
# 
# Since the first row in the file contains headers, we set --ignore-first=true
#
# The file ID is the first column (index = 0) and the transcripts
# are in the second column (index = 1); so setting --col-id and
# --col-trn to 0 and 1 respectively.
!./sctk score \
  --ignore-first=true \
  --delimiter="," \
  --col-id=0 \
  --col-trn=1 \
  --cer=true \
  --out=report \
  --ref=valid_ref.csv \
  --hyp=valid_pred.csv

In [15]:
display(HTML(open("./report/hyp1.trn.dtl", 'r').read().replace("\n", "<br>")))